In [1]:
import pandas as pd
import sqlite3
import requests
import numpy as np
import folium
import folium.plugins

http://www.poi-factory.com/node/17657

In [2]:
con = sqlite3.connect('Campsite_data.db')
query = ''' SELECT Campsite_Name, Latitude, Longitude FROM Sites WHERE Campsite_Name like '%RV%' AND Campsite_Name not like '%closed%' '''
df_RV = pd.read_sql_query(query,con).set_index('Campsite_Name').drop_duplicates()
con.close
df_RV


Latitude   Longitude
Campsite_Name                                                      
10 Acres Campground and RV Park               44.030277  -73.403468
1015 RV Park                                  26.145834  -97.958195
11 Bridges Campground and RV Park             51.415188 -112.632344
115 Creek Rest Area (no services)             58.716979 -124.912576
1202 Motor Inn and RV Park                    62.387044 -140.873463
...                                                 ...         ...
Zion RV and Campground                        37.236637 -112.856060
Zion West RV Park                             37.231969 -113.364556
Zion's Gate RV Resort                         37.170192 -113.373832
Zuni Village RV Park                          35.224768 -114.014515
Zunino/Jiggs Reservoir Recreation Area - BLM  40.457238 -115.653227

[5311 rows x 2 columns]

In [3]:
df_RV.describe

<bound method NDFrame.describe of                                                Latitude   Longitude
Campsite_Name                                                      
10 Acres Campground and RV Park               44.030277  -73.403468
1015 RV Park                                  26.145834  -97.958195
11 Bridges Campground and RV Park             51.415188 -112.632344
115 Creek Rest Area (no services)             58.716979 -124.912576
1202 Motor Inn and RV Park                    62.387044 -140.873463
...                                                 ...         ...
Zion RV and Campground                        37.236637 -112.856060
Zion West RV Park                             37.231969 -113.364556
Zion's Gate RV Resort                         37.170192 -113.373832
Zuni Village RV Park                          35.224768 -114.014515
Zunino/Jiggs Reservoir Recreation Area - BLM  40.457238 -115.653227

[5311 rows x 2 columns]>

In [4]:
# create map of New York using latitude and longitude values
latitude = df_RV['Latitude'].mean()
longitude = df_RV['Longitude'].mean()
map_national_RV_parks = folium.Map(location=[latitude, longitude], zoom_start=4)

# add markers to map
marker_cluster = folium.plugins.MarkerCluster().add_to(map_national_RV_parks)
for lat, lng, name in zip(df_RV['Latitude'], df_RV['Longitude'], df_RV.reset_index()['Campsite_Name']):
    label = "<a  target='_blank' href='https://www.google.com/search?q={}'>{}</a>".format(name.replace(' ','%20'),name)
    #label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(marker_cluster)  

map_national_RV_parks

In [6]:
map_national_RV_parks.save('RV_Parks_Map.html')

In [11]:

VERSION = '20180604'
LIMIT = 60
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 24XQ2KIMXRYFZEWHRQZ1TSNKKDPFSLILAR1QNI1XPZREE5IF
CLIENT_SECRET:4USSMOW03WWKLQEU5RWGMFPD3RSTDCNUS2KUUB0HEYUMAJGT


In [17]:
try:
    con = sqlite3.connect('Campsite_data.db')
    query = ''' SELECT distinct(Venues) FROM Venues'''.format(name)
    completed_venues = pd.read_sql_query(query,con)['Venues'].tolist()
    con.close
except:
    completed_venues = []
    
print('Number of completed venues that will not be run again: {}'.format(len(completed_venues)))
for key, item in df_RV.reset_index().iterrows():
    venues_list = []
    print(item['Campsite_Name'])
    
    # create the API request URL
    url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
        CLIENT_ID, 
        CLIENT_SECRET, 
        VERSION, 
        item['Latitude'], 
        item['Longitude'], 
        10000, #radius
        LIMIT)
    
    if not (item['Campsite_Name'] in completed_venues):
        results = requests.get(url).json()["response"]['groups'][0]['items']
        venues_list.append([{
            'Campsite_Name': item['Campsite_Name'], 
            'Latitude': item['Latitude'], 
            'Longitude': item['Longitude'], 
            'Venue':v['venue']['name'], 
            'Venue Latitude':v['venue']['location']['lat'], 
            'Venue Longitude':v['venue']['location']['lng'],  
            'Venue Category':v['venue']['categories'][0]['name']} for v in results])
        
        nearby_venues = pd.DataFrame(venues_list)
        con = sqlite3.connect('Campsite_data.db')
        nearby_venues.to_sql('Venues',con,if_exists='append')
        con.close()

Number of completed venues that will not be run again: 0
10 Acres Campground and RV Park


OperationalError: table Venues has no column named 0